In [1]:
import os
from glob import glob
import pathlib
import shutil

import earthpy.appeears as etapp
import earthpy as et
import earthpy.earthexplorer as etee
import earthpy.spatial as es
import geopandas as gpd
import geoviews as gv
import holoviews as hv
import hvplot.pandas
import hvplot.xarray
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import panel as pn
import requests
import rioxarray as rxr
import rioxarray.merge as rxrm
import xarray as xr
import xrspatial

data_dir = os.path.join(et.io.HOME, et.io.DATA_NAME)
project_dir = os.path.join(data_dir, 'grassland-analysis')
#ndvi_dir = os.path.join(data_dir, 'oakland-green-space', 'processed')

for a_dir in [data_dir, project_dir]:
    if not os.path.exists(a_dir):
        os.makedirs(a_dir)

### Habitat Suitability Modeling for Sorghastrum nutans

We are building a habitat suitability model for this grassland type. Research the grass and add information and citations here!

I am going to analyze the Pawnee National Grassland and Thunder Basin National Grassland units. This data is downloaded from here, make sure to provide a citation!

https://www.gbif.org/species/2704414

In [2]:
# Download grassland unit shapefile
gl_unit_path = os.path.join(
    data_dir,
    'earthpy-downloads',
    'S_USA.NationalGrassland',
    'S_USA.NationalGrassland.shp'
)
if not os.path.exists(gl_unit_path):
    print('downloading ' + gl_url)
    gl_url = ('https://data.fs.usda.gov/geodata/edw/'
              'edw_resources/shp/S_USA.NationalGrassland.zip')
    gl_zip = et.data.get_data(url=gl_url)
    
gl_unit_gdf = (
    gpd.read_file(gl_unit_path).set_index('GRASSLANDN')
    .loc[['Thunder Basin National Grassland', 'Pawnee National Grassland']]
    .to_crs(4326)
)
gl_unit_gdf

data_accumulator = {}

In [3]:
# Create site maps for each GL unit
gl_layout = hv.Layout()

for name, details in gl_unit_gdf.iterrows():
    gl_plot = gl_unit_gdf.loc[[name]].hvplot(
        geo=True, 
        tiles='EsriNatGeo',
        aspect='equal',
        width=600,
        height=400,
        line_color='black',
        fill_color='green',
        title='Site Map for ' + name
    )
    gl_layout+=gl_plot
gl_layout.cols(1).opts(shared_axes=False)


:Layout
   .Overlay.I  :Overlay
      .WMTS.I     :WMTS   [Longitude,Latitude]
      .Polygons.I :Polygons   [Longitude,Latitude]
   .Overlay.II :Overlay
      .WMTS.I     :WMTS   [Longitude,Latitude]
      .Polygons.I :Polygons   [Longitude,Latitude]

### Habitat Characteristics

We are going to use the following characteristics for the habitat model:

https://www.nrcs.usda.gov/plantmaterials/etpmcpg13196.pdf

- median silt soil percentage from 15cm to 30cm- http://hydrology.cee.duke.edu/POLARIS/PROPERTIES/v1.0/silt/p50/15_30/


In [4]:
# Download soils characteristic data

# Identify bounds of units to be able to select right file to download
for unit, details in gl_unit_gdf.iterrows():
    bbox = etee.BBox(*details.geometry.bounds)
    print(unit + ' ' +str(details.geometry.bounds))

soil_list = ['lat4344_lon-105-104.tif',
             'lat4344_lon-106-105.tif',
             'lat4445_lon-105-104.tif',
             'lat4445_lon-106-105.tif',
             'lat4041_lon-104-103.tif',
             'lat4041_lon-105-104.tif']

# Download soils data per the specified list above
for file in soil_list:
    file_path = os.path.join(
        data_dir,
        'earthpy-downloads',
        file
    )
    if not os.path.exists(file_path):
        print("Downloading " + file)
        url = ('http://hydrology.cee.duke.edu/POLARIS/'
        'PROPERTIES/v1.0/silt/p50/15_30/' + file
              )
        print(url)
        et.data.get_data(url=url)
    else:
        print(file + " already downloaded.")

# Merge and clip soils rasters
tif_paths = glob(os.path.join(
    data_dir,
    'earthpy-downloads',
    '*.tif')
)
# print(tif_paths)
print("attempting to merge soils rasters...")
das = [rxr.open_rasterio(tp, masked=True).squeeze() for tp in tif_paths]
merged_soils = rxrm.merge_arrays(das).rio.clip_box(*gl_unit_gdf.total_bounds)

merged_soils.hvplot(rasterize=True, x='x', y='y', aspect='equal')

data_accumulator['merged_soils'] = merged_soils
# Adding this da again as the template for harmonizing later on
data_accumulator['harmonizer'] = merged_soils
    

Thunder Basin National Grassland (-105.68534577740812, 43.13179205151148, -104.3147230581148, 44.78726284154685)
Pawnee National Grassland (-104.79144253125483, 40.609566404744555, -103.57328571411065, 41.001847062442295)
lat4344_lon-105-104.tif already downloaded.
lat4344_lon-106-105.tif already downloaded.
lat4445_lon-105-104.tif already downloaded.
lat4445_lon-106-105.tif already downloaded.
lat4041_lon-104-103.tif already downloaded.
lat4041_lon-105-104.tif already downloaded.
attempting to merge soils rasters...


In [61]:
# Download SRTM elevation data, save multiple arrays to a dictionary

aspect_list =[]
elev_path_list = []
for name, details in gl_unit_gdf.iterrows():
    print("Attempting to download SRTM data for " + name)
    download_key = name.replace(" ", "-")
    
    srtm_dir = os.path.join(
        data_dir,
        'earthpy-downloads',
        'Final-Project',
        'SRTM',
    )
    elev_path_list.append(srtm_dir + "/" + download_key)
    print (elev_path_list)                      
    dl_gdf = (
        gl_unit_gdf
        .loc[[name]]
    )

    # Initialize AppeearsDownloader for MODIS NDVI data
    srtm_downloader = etapp.AppeearsDownloader(
        download_key= download_key,
        ea_dir=srtm_dir,
        product='SRTMGL1_NC.003',
        layer='SRTMGL1_DEM',
        start_date="02-11-2000",
        end_date="02-21-2000",
        polygon=dl_gdf
    )
    # Download files if the download directory does not exist
    if not os.path.exists(srtm_downloader.data_dir):
        srtm_downloader.submit_task_request()
        print("Submitting download request for " + name)
        srtm_downloader.download_files()
    else:
        print("Data for " + name + " is already downloaded.")
    
    tif_paths = glob(
        os.path.join(
        srtm_downloader.data_dir,
            'SRTMGL1_NC.003*',
            '*.tif'
        )
    )
    
    elev_da = [rxr.open_rasterio(srtm_path, masked=True).squeeze() for srtm_path in tif_paths][0]
    elev_plot = elev_da.hvplot(    
        rasterize=True,
        x='x',
        y='y',
        aspect='equal',
        width=400,
        height=400
    )
    aspect_list.append(xrspatial.aspect(elev_da))

aspect_merged = rxrm.merge_arrays(aspect_list).rio.clip_box(*gl_unit_gdf.total_bounds)
aspect_plot = aspect_merged.hvplot(rasterize=True, x='x', y='y', aspect='equal')
data_accumulator['aspect_merged'] = aspect_merged
aspect_plot


Attempting to download SRTM data for Thunder Basin National Grassland
['C:\\Users\\Pete\\earth-analytics\\data\\earthpy-downloads\\Final-Project\\SRTM/Thunder-Basin-National-Grassland']
Data for Thunder Basin National Grassland is already downloaded.
Attempting to download SRTM data for Pawnee National Grassland
['C:\\Users\\Pete\\earth-analytics\\data\\earthpy-downloads\\Final-Project\\SRTM/Thunder-Basin-National-Grassland', 'C:\\Users\\Pete\\earth-analytics\\data\\earthpy-downloads\\Final-Project\\SRTM/Pawnee-National-Grassland']
Data for Pawnee National Grassland is already downloaded.


:DynamicMap   []
   :Image   [x,y]   (aspect)

In [62]:
# Download MACA climate model data
# 1990, CCSM4
# http://thredds.northwestknowledge.net:8080/thredds/reacch_climate_CMIP5_aggregated_macav2_monthly_catalog.html?dataset=agg_macav2metdata_pr_CCSM4_r6i1p1_historical_1950_2005_CONUS_monthly

maca_url = (
    'http://thredds.northwestknowledge.net:8080/thredds/ncss'
    '/agg_macav2metdata_pr_CCSM4_r6i1p1_historical_1950_2005_CONUS_monthly.nc'
    '?var=precipitation'
    '&disableLLSubset=on'
    '&disableProjSubset=on'
    '&horizStride=1'
    '&time_start=1990-01-15T00%3A00%3A00Z'
    '&time_end=1990-12-15T00%3A00%3A00Z'
    '&timeStride=1'
'&accept=netcdf'
)
maca_response = requests.get(maca_url)
print(maca_response)
with open('maca.nc', 'wb') as maca_file:
    maca_file.write(maca_response.content)
maca_ds = xr.open_dataset('maca.nc')
maca_ds = maca_ds.assign_coords(lon= maca_ds.lon-360)
precip_1990_da = maca_ds.precipitation
precip_1990_da.rio.write_crs("epsg:4326", inplace=True)
precip_1990_da.rio.set_spatial_dims('lon', 'lat', inplace=True)
# precip_2005_da.mean('time').hvplot(rasterize=True)

<Response [200]>


<xarray.DataArray 'precipitation' (time: 12, lat: 585, lon: 1386)>
[9729720 values with dtype=float32]
Coordinates:
  * time     (time) object 1990-01-15 00:00:00 ... 1990-12-15 00:00:00
  * lat      (lat) float64 25.06 25.1 25.15 25.19 ... 49.27 49.31 49.35 49.4
  * lon      (lon) float64 -124.8 -124.7 -124.7 -124.6 ... -67.15 -67.11 -67.06
    crs      int32 0
Attributes:
    long_name:      Monthly Precipitation Amount
    units:          mm
    grid_mapping:   crs
    standard_name:  precipitation
    cell_methods:   time: sum(interval: 24 hours): sum over days
    comments:       Total monthly precipitation at surface: includes both liq...
    _ChunkSizes:    [ 10  44 107]

In [63]:
precip_1990_clip = precip_1990_da.rio.clip_box(*gl_unit_gdf.total_bounds).mean('time')
precip_1990_plot = precip_1990_clip.hvplot()*gl_unit_gdf.hvplot(aspect='equal')
# Adding this da again as the template for harmonizing later on
data_accumulator['precip_1990_clip'] = precip_1990_clip    
precip_1990_plot


:Overlay
   .Image.I    :Image   [lon,lat]   (precipitation)
   .Polygons.I :Polygons   [x,y]

In [64]:
# Download MACA climate model data
# 2006-2099, use 2055, CCSM4
# http://thredds.northwestknowledge.net:8080/thredds/ncss/agg_macav2metdata_pr_CCSM4_r6i1p1_rcp45_2006_2099_CONUS_monthly.nc?var=precipitation&disableLLSubset=on&disableProjSubset=on&horizStride=1&time_start=2006-01-15T00%3A00%3A00Z&time_end=2099-12-15T00%3A00%3A00Z&timeStride=1&accept=netcdf
maca_url = (
    'http://thredds.northwestknowledge.net:8080/thredds/ncss'
    '/agg_macav2metdata_pr_CCSM4_r6i1p1_rcp45_2006_2099_CONUS_monthly.nc'
    '?var=precipitation&disableLLSubset=on'
    '&disableProjSubset=on'
    '&horizStride=1'
    '&time_start=2055-01-15T00%3A00%3A00Z'
    '&time_end=2055-12-15T00%3A00%3A00Z'
    '&timeStride=1'
    '&accept=netcdf'
)
maca_response = requests.get(maca_url)
print(maca_response)
with open('maca.nc', 'wb') as maca_file:
    maca_file.write(maca_response.content)
maca_ds = xr.open_dataset('maca.nc')
maca_ds = maca_ds.assign_coords(lon= maca_ds.lon-360)
precip_2055_da = maca_ds.precipitation
precip_2055_da.rio.write_crs("epsg:4326", inplace=True)
precip_2055_da.rio.set_spatial_dims('lon', 'lat', inplace=True)

# precip_2055_da.mean('time').hvplot(rasterize=True)

<Response [200]>


<xarray.DataArray 'precipitation' (time: 12, lat: 585, lon: 1386)>
[9729720 values with dtype=float32]
Coordinates:
  * time     (time) object 2055-01-15 00:00:00 ... 2055-12-15 00:00:00
  * lat      (lat) float64 25.06 25.1 25.15 25.19 ... 49.27 49.31 49.35 49.4
  * lon      (lon) float64 -124.8 -124.7 -124.7 -124.6 ... -67.15 -67.11 -67.06
    crs      int32 0
Attributes:
    long_name:      Monthly Precipitation Amount
    units:          mm
    grid_mapping:   crs
    standard_name:  precipitation
    cell_methods:   time: sum(interval: 24 hours): sum over days
    comments:       Total monthly precipitation at surface: includes both liq...
    _ChunkSizes:    [ 10  44 107]

In [65]:
precip_2055_clip = precip_2055_da.rio.clip_box(*gl_unit_gdf.total_bounds).mean('time')
precip_2055_plot = precip_2055_clip.hvplot()*gl_unit_gdf.hvplot(aspect='equal')
data_accumulator['precip_2055_clip'] = precip_2055_clip  
precip_2055_plot

:Overlay
   .Image.I    :Image   [lon,lat]   (precipitation)
   .Polygons.I :Polygons   [x,y]

- harmonize data with s.rio.reproject_match() method from rioxarray.
- perform raster multiplication of optimized conditions
- compare to GL units
- need different year for MACA data?

In [93]:
# Function to harmonize grid data

def harmonize_grids(accumulator_dict):
    """
    Harmonize all grid data inputs for the habitat model

    Parameters
    ==========
    accumulator_list : dict
      A dictionary containing data arrays to harmonize.
      The key is the variable name used above.
      The value is the data array.

    Returns
    =======
    harmonized_dict : dict
      Updated dictionary with harmonized data arrays replacing input.
    """
    harmonize_da = accumulator_dict['harmonizer']
    harmonized_dict = {}
    for key in accumulator_dict:
        da = accumulator_dict[key]
        da.rio.write_crs("epsg:3857", inplace=True)
        harmonized_da = da.rio.reproject_match(harmonize_da)
        harmonized_dict[key] = harmonized_da
    #harmonized_dict = accumulator_dict
    del harmonized_dict['harmonizer']
    print(harmonized_dict)

    return harmonized_dict


In [94]:
harmonized_grids = harmonize_grids(data_accumulator)

{'merged_soils': <xarray.DataArray (y: 15041, x: 7605)>
array([[31.5, 37.5, 36.5, ...,  nan,  nan,  nan],
       [32.5, 32.5, 32.5, ...,  nan,  nan,  nan],
       [33.5, 33.5, 16.5, ...,  nan,  nan,  nan],
       ...,
       [ nan,  nan,  nan, ..., 33.5, 23.5, 19.5],
       [ nan,  nan,  nan, ..., 18.5, 30.5, 28.5],
       [ nan,  nan,  nan, ..., 16.5, 30.5, 36.5]], dtype=float32)
Coordinates:
    band         int32 1
    spatial_ref  int32 0
  * x            (x) float64 -105.7 -105.7 -105.7 ... -103.6 -103.6 -103.6
  * y            (y) float64 44.79 44.79 44.79 44.79 ... 40.61 40.61 40.61 40.61
Attributes:
    AREA_OR_POINT:  Area
    scale_factor:   1.0
    add_offset:     0.0
    _FillValue:     nan, 'aspect_merged': <xarray.DataArray 'aspect' (y: 15041, x: 7605)>
array([[          nan,           nan,           nan, ..., 0.0000000e+00,
        0.0000000e+00, 3.4028235e+38],
       [          nan, 2.4498311e+02, 2.4025511e+02, ..., 0.0000000e+00,
        0.0000000e+00, 3.4028235e+38]

In [113]:
# harmonize_da = data_accumulator['harmonizer']
# test_da = data_accumulator['aspect_merged'].rio.reproject_match(harmonize_da)
harmonized_grids['aspect_merged'].rio.reproject('epsg:3857')
harmonized_grids['aspect_merged'].hvplot(rasterize=True, aspect='equal', cmap='colorwheel')
# data_accumulator['aspect_merged'].hvplot(rasterize=True, aspect='equal')
#harmonized_grids['aspect_merged'].hvplot(rasterize=True)
# test_da = ((harmonized_grids['aspect_merged'] >= 157.5) & (harmonized_grids['aspect_merged'] <= 202.5))
# test_da = test_da.astype(int)
# test_da.hvplot(rasterize=True, aspect='equal')
#harmonized_grids['aspect_merged']

C:\Users\Pete\miniconda3\envs\earth-analytics-python\lib\site-packages\rioxarray\raster_writer.py:130: UserWarning: The nodata value (3.402823466e+38) has been automatically changed to (3.4028234663852886e+38) to match the dtype of the data.
  warnings.warn(


:DynamicMap   []
   :Image   [x,y]   (aspect)

In [110]:
# Function to optimize habitat data for model analysis
# Convert raster values to boolean; False is not optimal condition, True is optimal condition

def optimize_habitat_data(accumulator_dict, opt_soil_range, opt_aspect_range, opt_precip_range):
    """
    Convert habitat rasters to boolean format for analysis.
    Parameters will be a dicitonary containing harmonized rasters
    and value ranges for optimal habitat.

    Parameters
    ==========
    accumulator_list : dict
      A dictionary containing data arrays to optimize.
      This dictionary should be the output from harmonize_grids().
      The key is the variable name used above.
      The value is the data array.
    opt_soil_range : list
      List with two values specifiying optimal soil percentage range.
      First value is low value, second is high value.
    opt_aspect_range : list
      List with two values specifiying optimal aspect degree range.
      First value is low value, second is high value.
    opt_precip_range : list
      List with two values specifiying optimal precipitation range in cm.
      First value is low value, second is high value.

    Returns
    =======
    optimized_dict : dict
      Updated dictionary with optimized data arrays replacing input.
    """
    optimized_dict = {}
    for key in accumulator_dict:
        if key == 'merged_soils':
            da = accumulator_dict[key]
            da = ((da >= opt_soil_range[0]) & (da <= opt_soil_range[1]))
            da = da.astype(int)
            optimized_dict[key] = da
        if key == 'aspect_merged':
            da = accumulator_dict[key]
            da = ((da.attrs['aspect'] >= opt_aspect_range[0]) & (da.aspect <= opt_aspect_range[1]))
            da = da.astype(int)
            optimized_dict[key] = da
        if key == 'precip_1990_clip':
            da = accumulator_dict[key]
            da = ((da >= opt_precip_range[0]) & (da <= opt_precip_range[1]))
            da = da.astype(int)
            optimized_dict[key] = da
        if key == 'precip_2055_clip':
            da = accumulator_dict[key]
            da = ((da >= opt_precip_range[0]) & (da <= opt_precip_range[1]))
            da = da.astype(int)
            optimized_dict[key] = da

    return optimized_dict

In [111]:
# Manually update the optimal habitat range lists here to input as parameters to function
# Select precipitation values from array that exceed threshold; 1=possible indian grass, 0=not possible
# Indiangrass precipitation values are found here: https://www.nrcs.usda.gov/plantmaterials/etpmcpg13196.pdf
# Select sand values from array that exceed threshold; 1=possible indian grass, 0=not possible
# Soil type diagram can be found here: https://en.wikipedia.org/wiki/Loam#/media/File:SoilTexture_USDA.svg
# Select aspect values from array that exceed threshold; 1=possible indian grass, 0=not possible
# Reference for aspect values can be found here https://desktop.arcgis.com/en/arcmap/10.3/tools/spatial-analyst-toolbox/how-aspect-works.htm#ESRI_SECTION1_4198691F8852475A9F4BC71246579FAA
opt_soil_range = [0,50]
opt_aspect_range = [157.5,202.5]
opt_precip_range = [28,114]

optimized_grids = optimize_habitat_data(harmonized_grids, opt_soil_range, opt_aspect_range, opt_precip_range)
optimized_grids
#optimized_grids['merged_soils']
#optimized_grids['aspect_merged']

KeyError: 'aspect'

In [100]:
harmonized_grids['aspect_merged'].hvplot(rasterize=True, aspect='equal') #* optimized_grids['aspect_merged'] #* optimized_grids['precip_1990_clip'] * optimized_grids['precip_2055_clip']

# habitat_grid = optimized_grids['merged_soils']
# for key, data_array in optimized_grids.items():
#     if key != 'merged_soils':
#         habitat_grid *= data_array
        

:DynamicMap   []
   :Image   [x,y]   (aspect)

In [30]:
habitat_plot = habitat_grid.hvplot(rasterize=True, x ='x', y='y')*gl_unit_gdf.hvplot(aspect='equal')
habitat_plot

:DynamicMap   []
   :Overlay
      .Image.I    :Image   [x,y]   (value)
      .Polygons.I :Polygons   [x,y]